In [2]:
import numpy as np
from matplotlib import pylab as pl
import scipy.linalg as la
%matplotlib

Using matplotlib backend: Qt5Agg


In [3]:
def Create_ChiMax(d, L, chi):
    """
    Create the variable dimension of the chi over the chain
    d - local Hilbert space dimension
    L - length of the chain
    chi - maximum allowed value of chi
    """
    vv = np.zeros(L, dtype=int)
    for i in range(L):
        vv[i] = min ( d**(i+1), d**(L-i-1), chi)
    
    return vv[::-1]

def Make_RightNormalizedB_L(L, d, chi_max, ChiM):
    """
    This create/initialized B matrices as 
    right normalized matrix
    
    L- system size
    d- local hilbert space dimension
    chi_max - maximum bond dimension
    ChiM    - distribution of chi over the chain
    """
    # contains all the right normalized B
    Blist=[]  #<-- final list 
    M_list=[] #<-- local list of M matrices (open boundary condition)
    
    # make Mlist here (starting from random numbers)
    for i in range(L):
        if i == 0 :
            M_list.append(np.random.rand(d,1,chi_max))
        elif i == L-1:
            M_list.append(np.random.rand(d,chi_max,1))
        else:    
            M_list.append(np.random.rand(d,chi_max,chi_max))  
    
    # main loop for normalization
    for i in range(L):
        # index for list 
        idx = L-1-i
        # shapes
        a = M_list[idx].shape[1]
        b = M_list[idx].shape[0]
        c = M_list[idx].shape[2]
    
        # reshape and transpose
        B_tmp = np.reshape(np.transpose(M_list[idx], (1, 0, 2)), (a, b*c))
        X,Y,Z = np.linalg.svd(B_tmp,full_matrices=True, compute_uv=True)
  
        # new B
        B_new = np.reshape(Z[:ChiM[idx]], (ChiM[idx], d, Z.shape[1]//d))
        
        # add blist 
        Blist.append(np.transpose(B_new, (1,0,2)))
    
        # for next B
        X = X[:,0:ChiM[idx]]
        Y = Y[:ChiM[idx]]
        # XY dot
        Umat = np.dot(X, np.diag(Y))/la.norm(Y)
     
        # re multiply to M_list
        M_list[idx-1] = np.tensordot(M_list[idx-1], Umat, axes=(2,0))
        
        
    return Blist[::-1]


def CheckNormalization(Bl, L, dd=0):
    """
    It Checks the normaliztaion of the matrix
    given a list 
    
    Bl -- the Bmatrix list 
    L  -- system size (go through all the b-matrix)
    dd -- which diagonal entry
    
    """
    for i in range(L):
        print (np.diag(np.tensordot(Bl[i], Bl[i].T, ([0,2],[2,0])),dd))

In [60]:
chimax=100;d=2; L=20;
ChiVec = Create_ChiMax(d, L, chimax)

Bmat = Make_RightNormalizedB_L(L, d, chimax, ChiVec)

In [61]:
pl.plot(ChiVec, '--x')

In [51]:
Bmat[0].shape

(2, 1, 2)

In [53]:
Bmat[4].shape

(2, 16, 32)

In [58]:
CheckNormalization(Bmat, L, dd=0)

[1.]
[1. 1.]
[1. 1. 1. 1.]
[1. 1. 1. 1. 1. 1. 1. 1.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 

# Compress a state to MPS

In [88]:
#def compress(psi, L, chimax):
L=14;
psi= np.random.random(2**L)

def compress_state(psi, L, chimax):
    psi_aR = np.reshape(psi, (1, 2**L))
    Ms = []
    for n in range(1, L+1):
        chi_L, dim_R = psi_aR.shape

        # first reshape
        psi_LR = np.reshape(psi_aR, (chi_L*2, dim_R//2))

        # SVD
        M_n, lambda_n, psi_tilde = la.svd(psi_LR, \
                                                    full_matrices=False, \
                                                    lapack_driver='gesvd')
        # check chimax condition
        if len(lambda_n) > chimax:
            keep = np.argsort(lambda_n)[::-1][:chimax]

            ## keeping that many states
            M_n = M_n[:, keep]
            lambda_n = lambda_n[keep]
            psi_tilde = psi_tilde[keep, :]

        chi_np1 = len(lambda_n)
        M_n = np.reshape(M_n, (chi_L, 2, chi_np1))
        Ms.append(M_n)
        psi_aR = lambda_n[:, np.newaxis] * psi_tilde[:, :]
    return Ms

In [89]:
Ms = compress_state(psi, L, 40)
Mr = compress_state(psi, L, (2**L)//2)

print(2**L, (2**L)//2)

16384 8192


# overlap with original chi without truncation

In [90]:
def overlap(mps_b, mps_k):
    L = len(mps_b)
    
    contr = np.ones((1,1)) # has indices (alpha_n*, alpha_n)
    
    for n in range(L):
        M_k = mps_k[n]  # has indices (alpha_n, j_n, alpha_{n+1})
        contr = np.tensordot(contr, M_k , axes=(1, 0)) 

        # now contr has indices alpha_n*, j_n, alpha_{n+1}
        M_b = mps_b[n].conj()  # has indices (alpha_n*, j_n, alpha_{n+1}*)
        contr = np.tensordot(M_b, contr, axes=([0, 1], [0, 1]))
    
    return contr.item()

In [91]:
overlap(Ms, Mr)

0.9479371161043822

In [92]:
aa=np.sum([Ms[i].size for i in range(L)])
bb=np.sum([Mr[i].size for i in range(L)])

print(aa, bb)

14248 43688
